In [1]:
import json
import re

In [2]:
import sys


Likelihood = {}
Transition = {}
trans_prob = {}
emiss_prob = {}


In [3]:
def train(train_file):
    ftr = open(train_file, 'r')
    previous = "Begin_Sent"
    for line in ftr:
        if line.strip(): #if a line is not empty 

            word,tag = line.strip().split("\t") 

            if previous not in Transition: #create 2-D hashtable for transition
                Transition[previous] = {}
                if tag not in Transition[previous]:
                    Transition[previous][tag] = 1
                else:
                    Transition[previous][tag] += 1
            else:
                if tag not in Transition[previous]:
                    Transition[previous][tag] = 1
                else:
                    Transition[previous][tag] += 1


            if tag not in Likelihood: #create 2-D hashtable for emission 
                Likelihood[tag] = {}
                if word not in Likelihood[tag]:
                    Likelihood[tag][word] = 1
                else:
                    Likelihood[tag][word] += 1
            else:
                if word not in Likelihood[tag]:
                    Likelihood[tag][word] = 1
                else:
                    Likelihood[tag][word] += 1

            previous = tag

        if line in ['\n', '\r\n']: #if a line is empty

            if previous not in Transition:
                Transition[previous] = {}
                if "End_Sent" not in Transition[previous]:
                    Transition[previous]["End_Sent"] = 1
                else:
                    Transition[previous]["End_Sent"] += 1
            else:
                if "End_Sent" not in Transition[previous]:
                    Transition[previous]["End_Sent"] = 1
                else:
                    Transition[previous]["End_Sent"] += 1

            previous = "Begin_Sent"
            
    #calculate the transition probability
    for key, transition_dict in Transition.items():
        total = 0
        for tag, count in transition_dict.items():
            total += count 

        for tag, cnt in transition_dict.items():
            if tag not in trans_prob:
                trans_prob[tag] = {}
                trans_prob[tag][key] = cnt / total
            else:
                trans_prob[tag][key] = cnt / total
                
    #calculate the emission probability
    for tag, emission_dict in Likelihood.items():
        total = 0
        for word, cnt in emission_dict.items():
            total += cnt 

        for word, cnt in emission_dict.items():
            if word not in emiss_prob:
                emiss_prob[word] = {}
                emiss_prob[word][tag] = cnt / total
            else:
                emiss_prob[word][tag] = cnt / total

In [4]:
#To avoid the product exceed the  smallest number 
def product(num1,num2,num3):
    smallest = 4.4e-300
    product = num1*num2*num3
    if product <= smallest:
        return product * 100000
        #return smallest
    else:
        return product

In [5]:
def test(test_file):
    sentences = []
    ftr2 = open(test_file, 'r')
    temp = []
    for line in ftr2:
        if line.strip():
            word = line.strip()
            temp.append(word)

        if line in ['\n', '\r\n']:
            sentences.append(temp)
            temp = []
    
    #get possible tags
    possible_tags = []
    possible_tags.append("Begin_Sent")
    for tags in Likelihood.keys():
        possible_tags.append(tags)
    possible_tags.append("End_Sent")
    
    for sent in sentences:
        #create a 2-D array, columns are states, rows are words
        viterbi = []
        for i in range(len(possible_tags) + 1):
            viterbi.append([])
            for j in range(len(sent) + 3):
                viterbi[i].append(None)

        #fill out the states and words in the table, viterbi[0][0] is just a space 
        viterbi[0][0] = "space"
        viterbi[0][1] = 0
        viterbi[1][1] = 1 #Begin_Sent state is definite
        viterbi[0][-1] = len(viterbi[0]) - 2 
        for i in range(2, len(viterbi[0]) - 1):
            viterbi[0][i] = sent[i - 2]
        for j in range(1, len(viterbi)):
            viterbi[j][0] = possible_tags[j - 1]

        #Filling out states in position 1 

        #Handling OOV case 
        if viterbi[0][2] not in emiss_prob.keys():
            for n in range(2, len(viterbi)):
                if viterbi[n][0] == "End_Sent":
                    continue
                elif (viterbi[n][0] in Transition["Begin_Sent"].keys()):
                    viterbi[n][2] = trans_prob[viterbi[n][0]]['Begin_Sent']*(1/1000)
                else:
                    viterbi[n][2] = None
        else:
        #In vocabulary 
            for n in range(2, len(viterbi)):
                if viterbi[n][0] == "End_Sent":
                    continue
                elif viterbi[n][0] in Transition["Begin_Sent"].keys() and viterbi[n][0] in emiss_prob[viterbi[0][2]].keys():
                    viterbi[n][2] = trans_prob[viterbi[n][0]]['Begin_Sent'] * emiss_prob[viterbi[0][2]][viterbi[n][0]]
                else:
                    viterbi[n][2] = None
        
        #keep track of the pos tag we want to keep for the first token
        temp_track = {}
        backpointer = []
        for n in range(2, len(viterbi)):
            if viterbi[n][2] != None:
                temp_track[viterbi[n][0]] = viterbi[n][2]
        sorted_t = sorted(temp_track.items(), key = lambda d : d[1], reverse = True)
        backpointer.append(sorted_t[0][0])
        for k, v in sorted_t:
            temp_track[k] = v

        #Filling out other spaces (except end state) in viterbi and backpointer table 
        for col in range(3, len(viterbi[0])): #loop colomn by colomn
            #when reaching the last column:
            if viterbi[0][col] == len(viterbi[0]) - 2:
                for tag, value in temp_track.items(): #tag = previous tag 
                    if viterbi[len(viterbi)-1][col] == None or value > viterbi[len(viterbi)-1][col]:
                        viterbi[len(viterbi)-1][col] = value

            #rest of the tokens 
            else:
                #Not OOV
                if viterbi[0][col] in emiss_prob.keys(): #viterbi[0][col] = token 
                    #loop row by row, without reaching End_Sent
                    for row in range(2, len(viterbi) - 1):
                        if viterbi[row][0] in emiss_prob[viterbi[0][col]].keys(): #viterbi[row][0] = current tag
                            for tag, val in temp_track.items(): #tag = previous tag
                                #check if P(viterbi[row][0] | tag) exists 
                                if tag in trans_prob[viterbi[row][0]].keys():
                                    #calculate the temp_score, previous score * emiss_prob * trans_prob 
                                    temp_score = val * emiss_prob[viterbi[0][col]][viterbi[row][0]] * trans_prob[viterbi[row][0]][tag]

                                    #store the highest score in the slot 
                                    if viterbi[row][col] == None or temp_score > viterbi[row][col]:
                                        viterbi[row][col] = temp_score
                                
                                else: #error occurs when no matches for any word | POS, pos | previous pos pairs, then all of the columns would be none
                                    viterbi[row][col] = emiss_prob[viterbi[0][col]][viterbi[row][0]] * val * 1/1000


                else:
                #OOV
                    for row in range(2, len(viterbi)-1):
                        for tag, val in temp_track.items():
                            if tag in trans_prob[viterbi[row][0]].keys():
                                #calculate the temp_score, previous score * emiss_prob * trans_prob 
                                temp_score = val * 1/1000 * trans_prob[viterbi[row][0]][tag]

                                #store the highest score in the slot 
                                if viterbi[row][col] == None or temp_score > viterbi[row][col]:
                                    viterbi[row][col] = temp_score
                                    
                            else: #error occurs when no matches for any word | POS, pos | previous pos pairs, then all of the columns would be none
                                    viterbi[row][col] = 1/1000 * val * 1/1000

                #reset the temp_track
                temp_track = {}
                for n in range(2, len(viterbi) - 1):
                    if viterbi[n][col] != None:
                        temp_track[viterbi[n][0]] = viterbi[n][col]
                sorted_t = sorted(temp_track.items(), key = lambda d : d[1], reverse = True)
                backpointer.append(sorted_t[0][0])
                for k, v in sorted_t:
                    temp_track[k] = v
        #append the pos tagger for the current sentence to all_pos
        all_pos.append(backpointer)


In [6]:
filename1 = "recipes_raw_nosource_ar.json" 
filename2 = "recipes_raw_nosource_epi.json" 
filename3 = "recipes_raw_nosource_fn.json" 

In [7]:
with open(filename1, "r") as json_file:
    data = json.load(json_file)

In [8]:
data

{'rmK12Uau.ntP510KeImX506H6Mr6jTu': {'title': 'Slow Cooker Chicken and Dumplings',
  'ingredients': ['4 skinless, boneless chicken breast halves ADVERTISEMENT',
   '2 tablespoons butter ADVERTISEMENT',
   '2 (10.75 ounce) cans condensed cream of chicken soup ADVERTISEMENT',
   '1 onion, finely diced ADVERTISEMENT',
   '2 (10 ounce) packages refrigerated biscuit dough, torn into pieces ADVERTISEMENT',
   'ADVERTISEMENT'],
  'instructions': 'Place the chicken, butter, soup, and onion in a slow cooker, and fill with enough water to cover.\nCover, and cook for 5 to 6 hours on High. About 30 minutes before serving, place the torn biscuit dough in the slow cooker. Cook until the dough is no longer raw in the center.\n',
  'picture_link': '55lznCYBbs2mT8BTx6BTkLhynGHzM.S'},
 '5ZpZE8hSVdPk2ZXo1mZTyoPWJRSCPSm': {'title': 'Awesome Slow Cooker Pot Roast',
  'ingredients': ['2 (10.75 ounce) cans condensed cream of mushroom soup ADVERTISEMENT',
   '1 (1 ounce) package dry onion soup mix ADVERTISEME

In [6]:
for value in data.values():
    print(value["ingredients"])

['4 skinless, boneless chicken breast halves ADVERTISEMENT', '2 tablespoons butter ADVERTISEMENT', '2 (10.75 ounce) cans condensed cream of chicken soup ADVERTISEMENT', '1 onion, finely diced ADVERTISEMENT', '2 (10 ounce) packages refrigerated biscuit dough, torn into pieces ADVERTISEMENT', 'ADVERTISEMENT']
['2 (10.75 ounce) cans condensed cream of mushroom soup ADVERTISEMENT', '1 (1 ounce) package dry onion soup mix ADVERTISEMENT', '1 1/4 cups water ADVERTISEMENT', '5 1/2 pounds pot roast ADVERTISEMENT', 'ADVERTISEMENT']
['1/2 cup packed brown sugar ADVERTISEMENT', '1/2 cup ketchup ADVERTISEMENT', '1 1/2 pounds lean ground beef ADVERTISEMENT', '3/4 cup milk ADVERTISEMENT', '2 eggs ADVERTISEMENT', '1 1/2 teaspoons salt ADVERTISEMENT', '1/4 teaspoon ground black pepper ADVERTISEMENT', '1 small onion, chopped ADVERTISEMENT', '1/4 teaspoon ground ginger ADVERTISEMENT', '3/4 cup finely crushed saltine cracker crumbs ADVERTISEMENT', 'ADVERTISEMENT']
['1 cup butter, softened ADVERTISEMENT', 

['4 tablespoons butter ADVERTISEMENT', '1 clove garlic, minced ADVERTISEMENT', '3 (3/4 inch thick) slices French bread, cut into cubes ADVERTISEMENT', 'ADVERTISEMENT']
['6 thick slices bacon, chopped ADVERTISEMENT', '1/2 cup onions, minced ADVERTISEMENT', '1 teaspoon minced garlic ADVERTISEMENT', '1 pound fresh green beans, trimmed ADVERTISEMENT', '1 cup water ADVERTISEMENT', '1/8 teaspoon salt ADVERTISEMENT', '1 pinch ground black pepper ADVERTISEMENT', 'ADVERTISEMENT']
['1/2 cup rice vinegar ADVERTISEMENT', '5 tablespoons honey ADVERTISEMENT', '1/3 cup soy sauce (such as Silver Swan®) ADVERTISEMENT', '1/4 cup Asian (toasted) sesame oil ADVERTISEMENT', '3 tablespoons Asian chili garlic sauce ADVERTISEMENT', '3 tablespoons minced garlic ADVERTISEMENT', 'salt to taste ADVERTISEMENT', '8 skinless, boneless chicken thighs ADVERTISEMENT', '1 tablespoon chopped green onion (optional) ADVERTISEMENT', 'ADVERTISEMENT']
['3 tablespoons olive oil ADVERTISEMENT', '3 pounds Italian sausage links A

['1/2 pound ground pork sausage ADVERTISEMENT', '1 (8 ounce) package cream cheese, softened ADVERTISEMENT', '1 (8 ounce) package fresh mushrooms, stems removed ADVERTISEMENT', 'ADVERTISEMENT']
['6 roma (plum) tomatoes, diced ADVERTISEMENT', '1 small cucumber - peeled, quartered lengthwise, and chopped ADVERTISEMENT', '3 green onions, chopped ADVERTISEMENT', '1/4 cup fresh basil leaves, cut into thin strips ADVERTISEMENT', '3 tablespoons olive oil ADVERTISEMENT', '2 tablespoons balsamic vinegar ADVERTISEMENT', '3 tablespoons crumbled feta cheese ADVERTISEMENT', 'salt and freshly ground black pepper to taste ADVERTISEMENT', 'ADVERTISEMENT']
['2 teaspoons hot chili powder ADVERTISEMENT', '1 1/2 teaspoons paprika ADVERTISEMENT', '1 teaspoon onion powder ADVERTISEMENT', '1/2 teaspoon sea salt ADVERTISEMENT', '1/2 teaspoon garlic powder ADVERTISEMENT', '1/2 teaspoon ground cumin ADVERTISEMENT', '1/2 teaspoon oregano ADVERTISEMENT', '1/4 teaspoon freshly ground black pepper, or to taste ADVER

['1 (16 ounce) package garden herb tofu, crumbled ADVERTISEMENT', '2 tablespoons vegetable oil ADVERTISEMENT', '1 clove garlic, minced ADVERTISEMENT', '1/2 cup chopped onion ADVERTISEMENT', '2 teaspoons chili powder ADVERTISEMENT', '1/4 teaspoon paprika ADVERTISEMENT', '1/4 teaspoon cayenne pepper ADVERTISEMENT', '1/4 teaspoon ground cumin ADVERTISEMENT', '1/4 teaspoon salt ADVERTISEMENT', '1/2 lime, juiced ADVERTISEMENT', '1/2 cup tomato sauce ADVERTISEMENT', '1/4 cup chopped fresh cilantro ADVERTISEMENT', '10 medium taco shells, heated ADVERTISEMENT', '2 cups shredded lettuce ADVERTISEMENT', '2 tomatoes, chopped ADVERTISEMENT', '1 avocado - peeled, pitted and diced ADVERTISEMENT', '1 cup shredded Cheddar cheese ADVERTISEMENT', '1/4 cup salsa ADVERTISEMENT', 'ADVERTISEMENT']
['1 cup dry lentils ADVERTISEMENT', '1 quart water ADVERTISEMENT', '1 cube vegetable bouillon ADVERTISEMENT', '3 medium tomatoes, peeled and diced ADVERTISEMENT', '1 large onion, diced ADVERTISEMENT', '1 carrot, s

KeyError: 'ingredients'

In [9]:
ingredients = {}
instructions = {}
check = False
for recipe in data.values():
    
    for keys in recipe.keys():
        if keys == "title":
            check = True
   
    if check == True:
        title = recipe["title"] 
    else:
        continue
        
    check = False
    
    ingredients[title] = recipe["ingredients"]
    instructions[title] = recipe["instructions"]
    

In [10]:
for ingre_list in ingredients.values():
    for i in range(len(ingre_list)):
        ingre_list[i] = ingre_list[i].strip("ADVERTISEMENT ")

In [11]:
ingredients

{'Slow Cooker Chicken and Dumplings': ['4 skinless, boneless chicken breast halves',
  '2 tablespoons butter',
  '2 (10.75 ounce) cans condensed cream of chicken soup',
  '1 onion, finely diced',
  '2 (10 ounce) packages refrigerated biscuit dough, torn into pieces',
  ''],
 'Awesome Slow Cooker Pot Roast': ['2 (10.75 ounce) cans condensed cream of mushroom soup',
  '1 (1 ounce) package dry onion soup mix',
  '1 1/4 cups water',
  '5 1/2 pounds pot roast',
  ''],
 'Brown Sugar Meatloaf': ['1/2 cup packed brown sugar',
  '1/2 cup ketchup',
  '1 1/2 pounds lean ground beef',
  '3/4 cup milk',
  '2 eggs',
  '1 1/2 teaspoons salt',
  '1/4 teaspoon ground black pepper',
  '1 small onion, chopped',
  '1/4 teaspoon ground ginger',
  '3/4 cup finely crushed saltine cracker crumbs',
  ''],
 'Best Chocolate Chip Cookies': ['1 cup butter, softened',
  '1 cup white sugar',
  '1 cup packed brown sugar',
  '2 eggs',
  '2 teaspoons vanilla extract',
  '3 cups all-purpose flour',
  '1 teaspoon baking 

In [12]:
instructions

{'Slow Cooker Chicken and Dumplings': 'Place the chicken, butter, soup, and onion in a slow cooker, and fill with enough water to cover.\nCover, and cook for 5 to 6 hours on High. About 30 minutes before serving, place the torn biscuit dough in the slow cooker. Cook until the dough is no longer raw in the center.\n',
 'Awesome Slow Cooker Pot Roast': 'In a slow cooker, mix cream of mushroom soup, dry onion soup mix and water. Place pot roast in slow cooker and coat with soup mixture.\nCook on High setting for 3 to 4 hours, or on Low setting for 8 to 9 hours.\n',
 'Brown Sugar Meatloaf': 'Preheat oven to 350 degrees F (175 degrees C). Lightly grease a 5x9 inch loaf pan.\nPress the brown sugar in the bottom of the prepared loaf pan and spread the ketchup over the sugar.\nIn a mixing bowl, mix thoroughly all remaining ingredients and shape into a loaf. Place on top of the ketchup.\nBake in preheated oven for 1 hour or until juices are clear.\n',
 'Best Chocolate Chip Cookies': 'Preheat ov

In [13]:
new_string = instructions['Slow Cooker Chicken and Dumplings'].replace("\n", " ")
f = open("test_txt.txt","w")
for token in new_string.strip().split(" "):
    if token[-1] == ",":
        f.write(token[:-1] + "\n"+ token[-1] + "\n")
    elif token[-1] == ".":
        f.write(token[:-1] + "\n"+ token[-1] + "\n\n")
    else:
        f.write(token + "\n")
f.close()

In [14]:
noun_list = []
ftr = open("output.txt", 'r')
for line in ftr:
    
    if line in ['\n', '\r\n']:
        continue
        
    word, tag = line.strip().split('\t')
    
    if "NN" in tag:
        noun_list.append(word)


In [15]:
noun_list

['chicken',
 'butter',
 'soup',
 'onion',
 'water',
 'Cover',
 'hours',
 'High',
 'minutes',
 'place',
 'biscuit',
 'dough',
 'cooker',
 'Cook',
 'dough',
 'center']

In [16]:
tools_file = open("list_tools.txt",'r')
tools_list = []
for line in tools_file.readlines():
    tools_list.append(line.strip())

FileNotFoundError: [Errno 2] No such file or directory: 'list_tools.txt'

In [17]:
tools_list

NameError: name 'tools_list' is not defined

In [18]:
ingre_list = {}
for title in ingredients:
    data_list = ingredients[title]
    for food in data_list:
        food = re.sub('[^A-z]+', ' ',food )
        for res in food.split():
            if res in tools_list:
                continue
            elif res not in ingre_list:
                ingre_list[res] = 1
            else:
                ingre_list[res] += 1
                
ingre = sorted(ingre_list.items(), key=lambda d:d[1], reverse = True)

NameError: name 'tools_list' is not defined

In [19]:
new_ingre = []
for i, n in ingre:
    new_ingre.append(i)

NameError: name 'ingre' is not defined

In [20]:
new_ingre

[]

In [21]:
with open("training_file", 'w') as new_file:
    WSJ = open("WSJ_02-21.pos",'r')

    new_file.write(WSJ.read()) 

    for i in range(100):
        f1 = open("file1", 'r')
        f2 = open("file2", 'r')
        new_file.write(f1.read())
        new_file.write(f2.read())
    
new_file.close()

FileNotFoundError: [Errno 2] No such file or directory: 'WSJ_02-21.pos'

In [22]:
count = len(open("training_file").readlines(  ))
count

0

In [23]:
len(open("WSJ_02-21.pos").readlines(  ))

FileNotFoundError: [Errno 2] No such file or directory: 'WSJ_02-21.pos'

In [24]:
train("training_file")

In [25]:
with open("tools_answer.txt","a") as f:
    
    count = 0
    for title in instructions:
        tmp_f = open("temp.txt", 'w')
        count += 1

        if count <= 50:  
            continue;
        elif count > 80:
            break
        else:
            new_string = instructions[title].replace("\n", " ")
            #print(title)
            for token in new_string.strip().split(" "):
                if token[-1] == ",":
                    tmp_f.write(token[:-1] + "\n"+ token[-1] + "\n")
                elif token[-1] == ".":
                    tmp_f.write(token[:-1] + "\n"+ token[-1] + "\n\n")
                else:
                    tmp_f.write(token + "\n")
            
            test("temp.txt")
            f.write(str(count) + "\t" + title + "\n")
            for i in range(len(sentences)):
                for j in range(len(sentences[i])):
                    f.write(sentences[i][j] + "\t" + all_pos[i][j] + "\n")

                f.write("\n")
        
        sentences = []
        all_pos = []
        
f.close()

NameError: name 'sentences' is not defined

In [26]:
sentences

NameError: name 'sentences' is not defined

In [146]:
all_pos

[['VB', 'NN', 'TO', 'CD', 'NNS', 'NNP', 'NNP', 'NNS', 'NNP', '.'],
 ['VB', 'DT', 'LS', '.', 'JJ', 'NN', '.'],
 ['VB',
  'CD',
  'IN',
  'DT',
  'NNS',
  'IN',
  'NN',
  'IN',
  'DT',
  'JJ',
  'NN',
  'NN',
  '.'],
 ['VB', 'IN', 'DT', 'NN', 'IN', ',', 'CC', 'VB', 'DT', 'VBG', 'NNS', '.'],
 ['VB', 'IN', 'NN', 'CC', 'NN', 'TO', 'VB', '.'],
 ['IN', 'DT', 'JJ', 'NN', ',', 'VB', 'NN', 'IN', 'JJ', 'NN', '.'],
 ['VB',
  'IN',
  'DT',
  'NN',
  'CC',
  'NN',
  ',',
  'CC',
  'VB',
  'RB',
  'IN',
  'DT',
  'VB',
  'IN',
  'CD',
  'NN',
  '.'],
 ['VB', 'IN', 'NN', '.'],
 ['VB', 'IN', 'NN', 'VBZ', 'VBN', '.'],
 ['VB',
  'IN',
  'NN',
  'DT',
  'IN',
  'RB',
  ',',
  'CC',
  'VB',
  'VBG',
  'IN',
  'VBN',
  ',',
  'IN',
  'CD',
  'TO',
  'CD',
  'NNS',
  '.'],
 ['VB',
  'NN',
  'IN',
  'DT',
  'NNS',
  ',',
  'CC',
  'VB',
  'DT',
  'NN',
  'IN',
  'NN',
  'NN',
  '.'],
 ['VB', 'CD', 'CD', 'NNS', 'IN', 'DT', 'JJ', 'NN', '.'],
 ['VB', 'NN', 'TO', 'CD', 'NNS', 'NNP', 'NNP', 'NNS', 'NNP', '.'],
 ['

In [121]:
tools_sys = []
ftr = open("submission.pos", 'r')
for line in ftr:
    
    if line in ['\n', '\r\n']:
        continue
        
    word, tag = line.strip().split('\t')
    
    if "NN" in tag and word not in new_ingre:
        tools_sys.append(word)


In [122]:
tools_sys

['oven',
 '(200',
 'C)',
 'saucepan',
 'seconds',
 'oven',
 'oven',
 '(220',
 'C)',
 'saucepan',
 'bowl',
 'bowl',
 'oven',
 'instant-read',
 '(74',
 'C)',
 'bowl',
 'grate',
 'skillet',
 'cooker',
 'oven',
 'C)',
 'Place',
 'C)',
 'saucepan',
 'wire',
 'oven',
 'C)',
 'bowl',
 'salt;',
 'spoonfuls',
 'oven',
 'wire',
 'bowl',
 'skillet',
 'cooker',
 'oven',
 '(200',
 'C)',
 'oven',
 'saucepan',
 'raisins;',
 'oven',
 '(150',
 'C)',
 'bowl',
 'bowl',
 'saucepan',
 'heat;',
 'saucepan',
 'minutes;',
 'oven',
 '(175',
 'C)',
 'bowl',
 'bowl',
 '(175',
 'C)',
 'bowl',
 'oven',
 '(175',
 'C)',
 'oven',
 'Repeat',
 'oven',
 '(175',
 'C)',
 'saucepan',
 '(about',
 'Reserve',
 '3/4',
 'saucepan',
 'bowl',
 '3/4',
 'oven',
 'cooker;',
 'cooker',
 'bowl',
 "confectioners'",
 'Store',
 'oven',
 '(175',
 'C)',
 'bowl',
 'salt;',
 'teaspoonfuls',
 'Store',
 'long!',
 'bowl',
 'oven',
 '(200',
 'C)',
 'oven',
 'cooker',
 'bowl',
 'pepper;',
 'oven',
 '(175',
 'C)',
 'bowl',
 'bowl',
 'oven',
 'wire

In [ ]:
for element in tools_sys:
    

In [87]:
len(ingre_list)

6550